# Part V - Learning
## Project 5b - nim

[Course Link](https://cs50.harvard.edu/ai/)

[Project Instructions](https://cs50.harvard.edu/ai/projects/4/nim/)

## Instructions

See project instruction link for more detailed instructions.  

Recall that in the game Nim, we begin with some number of piles, each with some number of objects. Players take turns: on a player’s turn, the player removes any non-negative number of objects from any one non-empty pile. Whoever removes the last object loses.

There’s some simple strategy you might imagine for this game: if there’s only one pile and three objects left in it, and it’s your turn, your best bet is to remove two of those objects, leaving your opponent with the third and final object to remove. But if there are more piles, the strategy gets considerably more complicated. In this problem, we’ll build an AI to learn the strategy for this game through reinforcement learning. By playing against itself repeatedly and learning from experience, eventually our AI will learn which actions to take and which actions to avoid.

In particular, we’ll use Q-learning for this project. Recall that in Q-learning, we try to learn a reward value (a number) for every (state, action) pair. An action that loses the game will have a reward of -1, an action that results in the other player losing the game will have a reward of 1, and an action that results in the game continuing has an immediate reward of 0, but will also have some future reward.

How will we represent the states and actions inside of a Python program? A “state” of the Nim game is just the current size of all of the piles. A state, for example, might be [1, 1, 3, 5], representing the state with 1 object in pile 0, 1 object in pile 1, 3 objects in pile 2, and 5 objects in pile 3. An “action” in the Nim game will be a pair of integers (i, j), representing the action of taking j objects from pile i. So the action (3, 5) represents the action “from pile 3, take away 5 objects.” Applying that action to the state [1, 1, 3, 5] would result in the new state [1, 1, 3, 0] (the same state, but with pile 3 now empty).

Recall that the key formula for Q-learning is below. Every time we are in a state s and take an action a, we can update the Q-value Q(s, a) according to:

Q(s, a) <- Q(s, a) + alpha * (new value estimate - old value estimate)

In the above formula, alpha is the learning rate (how much we value new information compared to information we already have). The new value estimate represents the sum of the reward received for the current action and the estimate of all the future rewards that the player will receive. The old value estimate is just the existing value for Q(s, a). By applying this formula every time our AI takes a new action, over time our AI will start to learn which actions are better in any state.



In [45]:
import math
import random
import time


class Nim():

    def __init__(self, initial=[1, 3, 5, 7]):
        """
        Initialize game board.
        Each game board has
            - `piles`: a list of how many elements remain in each pile
            - `player`: 0 or 1 to indicate which player's turn
            - `winner`: None, 0, or 1 to indicate who the winner is
        """
        self.piles = initial.copy()
        self.player = 0
        self.winner = None

    @classmethod
    def available_actions(cls, piles):
        """
        Nim.available_actions(piles) takes a `piles` list as input
        and returns all of the available actions `(i, j)` in that state.

        Action `(i, j)` represents the action of removing `j` items
        from pile `i` (where piles are 0-indexed).
        """
        actions = set()
        for i, pile in enumerate(piles):
            for j in range(1, piles[i] + 1):
                actions.add((i, j))
        return actions

    @classmethod
    def other_player(cls, player):
        """
        Nim.other_player(player) returns the player that is not
        `player`. Assumes `player` is either 0 or 1.
        """
        return 0 if player == 1 else 1

    def switch_player(self):
        """
        Switch the current player to the other player.
        """
        self.player = Nim.other_player(self.player)

    def move(self, action):
        """
        Make the move `action` for the current player.
        `action` must be a tuple `(i, j)`.
        """
        pile, count = action

        # Check for errors
        if self.winner is not None:
            raise Exception("Game already won")
        elif pile < 0 or pile >= len(self.piles):
            raise Exception("Invalid pile")
        elif count < 1 or count > self.piles[pile]:
            raise Exception("Invalid number of objects")

        # Update pile
        self.piles[pile] -= count
        self.switch_player()

        # Check for a winner
        if all(pile == 0 for pile in self.piles):
            self.winner = self.player


class NimAI():

    def __init__(self, alpha=0.5, epsilon=0.1):
        """
        Initialize AI with an empty Q-learning dictionary,
        an alpha (learning) rate, and an epsilon rate.

        The Q-learning dictionary maps `(state, action)`
        pairs to a Q-value (a number).
         - `state` is a tuple of remaining piles, e.g. (1, 1, 4, 4)
         - `action` is a tuple `(i, j)` for an action
        """
        self.q = dict()
        self.alpha = alpha
        self.epsilon = epsilon
        
    def update(self, old_state, action, new_state, reward):
        """
        Update Q-learning model, given an old state, an action taken
        in that state, a new resulting state, and the reward received
        from taking that action.
        """
        old = self.get_q_value(old_state, action)
        best_future = self.best_future_reward(new_state)
        self.update_q_value(old_state, action, old, reward, best_future)

    def get_q_value(self, state, action):
        """
        Return the Q-value for the state `state` and the action `action`.
        If no Q-value exists yet in `self.q`, return 0.
        """
        if (tuple(state), action) in self.q:
            return self.q[(tuple(state), action)]
        return 0 
            
        
    def update_q_value(self, state, action, old_q, reward, future_rewards):
        """
        Update the Q-value for the state `state` and the action `action`
        given the previous Q-value `old_q`, a current reward `reward`,
        and an estimate of future rewards `future_rewards`.

        Use the formula:

        Q(s, a) <- old value estimate
                   + alpha * (new value estimate - old value estimate)

        where `old value estimate` is the previous Q-value,
        `alpha` is the learning rate, and `new value estimate`
        is the sum of the current reward and estimated future rewards.
        """
        new_q = old_q + self.alpha * ((reward + future_rewards) - old_q)
        self.q[(tuple(state), action)] = new_q
    
    
    def best_future_reward(self, state):
        """
        Get the best possible action in current state
        
        Given a state `state`, consider all possible `(state, action)`
        pairs available in that state and return the maximum of all
        of their Q-values.

        Use 0 as the Q-value if a `(state, action)` pair has no
        Q-value in `self.q`. If there are no available actions in
        `state`, return 0.
        """
        all_actions = Nim.available_actions(state)
        
        if all_actions:
            max_qval = -math.inf
            for action in all_actions:
                max_qval = max(max_qval, self.get_q_value(state, action))        
            return max_qval
        return 0 
            

    def choose_action(self, state, epsilon=True):
        """
        Given a state `state`, return an action `(i, j)` to take.

        If `epsilon` is `False`, then return the best action
        available in the state (the one with the highest Q-value,
        using 0 for pairs that have no Q-values).

        If `epsilon` is `True`, then with probability
        `self.epsilon` choose a random available action,
        otherwise choose the best action available.

        If multiple actions have the same Q-value, any of those
        options is an acceptable return value.
        """       
        all_actions = Nim.available_actions(state)                            
                                                                 
        max_qval = -math.inf
        max_pile = 0
        max_count = 0
            
        for action in all_actions: 
            current_qval = self.get_q_value(state, action)             
            if current_qval > max_qval:
                max_qval = current_qval
                max_pile = action[0]
                max_count = action[1]
        
        # AI should ideally choose a q_value > 0. If it can't, go ahead
        # and make a random move so that it can make mistakes and learn from them.
        if max_qval > 0:
            print(f'AI Q-Learning Choice: {state, (max_pile, max_count), max_qval}')
            return max_pile, max_count
             
        print('AI Made Random Choice')
        return random.choice(list(all_actions))

def train(n):
    """
    Train an AI by playing `n` games against itself.
    """

    player = NimAI()

    # Play n games
    for i in range(n):
        print(f"Playing training game {i + 1}")
        game = Nim()

        # Keep track of last move made by either player
        last = {
            0: {"state": None, "action": None},
            1: {"state": None, "action": None}
        }

        # Game loop
        while True:

            # Keep track of current state and action
            state = game.piles.copy()
            action = player.choose_action(game.piles)

            # Keep track of last state and action
            last[game.player]["state"] = state
            last[game.player]["action"] = action

            # Make move
            game.move(action)
            new_state = game.piles.copy()

            # When game is over, update Q values with rewards
            if game.winner is not None:
                player.update(state, action, new_state, -1)
                player.update(
                    last[game.player]["state"],
                    last[game.player]["action"],
                    new_state,
                    1
                )
                break

            # If game is continuing, no rewards yet
            elif last[game.player]["state"] is not None:
                player.update(
                    last[game.player]["state"],
                    last[game.player]["action"],
                    new_state,
                    0
                )

    print("Done training")

    # Return the trained AI
    print(player.q)
    return player


def play(ai, human_player=None):
    """
    Play human game against the AI.
    `human_player` can be set to 0 or 1 to specify whether
    human player moves first or second.
    """

    # If no player order set, choose human's order randomly
    if human_player is None:
        human_player = random.randint(0, 1)

    # Create new game
    game = Nim()

    # Game loop
    while True:

        # Print contents of piles
        print()
        print("Piles:")
        for i, pile in enumerate(game.piles):
            print(f"Pile {i}: {pile}")
        print()

        # Compute available actions
        available_actions = Nim.available_actions(game.piles)
        time.sleep(1)

        # Let human make a move
        if game.player == human_player:
            print("Your Turn")
            while True:
                pile = int(input("Choose Pile: "))
                count = int(input("Choose Count: "))
                if (pile, count) in available_actions:
                    break
                print("Invalid move, try again.")

        # Have AI make a move
        else:
            print("AI's Turn")
            pile, count = ai.choose_action(game.piles, epsilon=False)
            print(f"AI chose to take {count} from pile {pile}.")

        # Make move
        game.move((pile, count))

        # Check for winner
        if game.winner is not None:
            print()
            print("GAME OVER")
                    
            winner = "Human" if game.winner == human_player else "AI"
            print(f"Winner is {winner}")
            return

In [46]:
ai = train(10_000)

Playing training game 1
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
Playing training game 2
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
Playing training game 3
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
Playing training game 4
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
Playing training game 5
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
Playing training game 6
AI Made Random Choice
AI Made Random Choice
AI Made Random Choice
AI Made Random Choic

AI Q-Learning Choice: ([1, 3, 1, 1], (0, 1), 0.0106201171875)
AI Q-Learning Choice: ([0, 3, 1, 1], (1, 1), 0.48095703125)
AI Q-Learning Choice: ([0, 2, 1, 1], (1, 1), 0.498046875)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 0], (1, 1), 0.99609375)
AI Made Random Choice
Playing training game 218
AI Q-Learning Choice: ([1, 3, 5, 7], (2, 2), 0.7726100167360284)
AI Q-Learning Choice: ([1, 3, 3, 7], (3, 6), 0.03863525390625)
AI Q-Learning Choice: ([1, 3, 3, 1], (2, 2), 0.68304443359375)
AI Q-Learning Choice: ([1, 3, 1, 1], (0, 1), 0.25433349609375)
AI Q-Learning Choice: ([0, 3, 1, 1], (1, 1), 0.240478515625)
AI Q-Learning Choice: ([0, 2, 1, 1], (1, 1), 0.7470703125)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 0], (1, 1), 0.998046875)
AI Made Random Choice
Playing training game 219
AI Q-Learning Choice: ([1, 3, 5, 7], (2, 2), 0.7278272251648892)
AI Q-Learning Choice: ([1, 3, 3, 7], (3, 6), 0.146484375)
AI Q-Learning Choice: ([1, 3, 3, 1], (2, 2), 0.461761474609375)
AI Q

AI Q-Learning Choice: ([1, 3, 4, 2], (1, 2), 0.0037512372029370683)
AI Q-Learning Choice: ([1, 1, 4, 2], (2, 2), 0.7507271612530471)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 2, 2], (0, 1), 0.8123016357421875)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 0], (2, 1), 0.9998779296875)
AI Made Random Choice
Playing training game 382
AI Q-Learning Choice: ([1, 3, 5, 7], (3, 2), 0.054973849753248635)
AI Q-Learning Choice: ([1, 3, 5, 5], (3, 2), 0.5331534974642791)
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 1), 0.01485176367002787)
AI Q-Learning Choice: ([1, 3, 4, 3], (3, 1), 0.6584298359768057)
AI Q-Learning Choice: ([1, 3, 4, 2], (1, 2), 0.0018756186014685342)
AI Q-Learning Choice: ([1, 1, 4, 2], (2, 2), 0.7815143984976173)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 1, 2], (3, 2), 0.9374999999376996)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 0], (1, 1), 0.9999999999708962)
AI Made Random Choice
Playing training game 383
AI Q-Learning Choice: ([1, 3, 

AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 3], (3, 1), 0.8593730926513672)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 0, 2], (3, 1), 0.999969482421875)
AI Made Random Choice
Playing training game 476
AI Q-Learning Choice: ([1, 3, 5, 7], (3, 2), 0.0010048528233863906)
AI Q-Learning Choice: ([1, 3, 5, 5], (3, 2), 0.8569047762195842)
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 1), 0.00013411034184608318)
AI Q-Learning Choice: ([1, 3, 4, 3], (2, 2), 0.9134799257636813)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 2, 3], (0, 1), 0.9027271878293845)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 3], (3, 2), 0.7499999850979293)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 0], (1, 1), 0.999999999998181)
AI Made Random Choice
Playing training game 477
AI Q-Learning Choice: ([1, 3, 5, 7], (3, 2), 0.0005694815826162369)
AI Q-Learning Choice: ([1, 3, 5, 5], (3, 2), 0.8851923509916327)
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 1), 6.705517092304159e-05)
AI 

AI Q-Learning Choice: ([1, 1, 2, 3], (0, 1), 0.9130597229193285)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 2, 0], (2, 2), 0.9999980926513672)
AI Made Random Choice
Playing training game 588
AI Q-Learning Choice: ([1, 3, 5, 7], (3, 2), 3.584299957928767e-10)
AI Q-Learning Choice: ([1, 3, 5, 5], (3, 2), 0.9507303586492566)
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 1), 1.0145758730370102e-11)
AI Q-Learning Choice: ([1, 3, 4, 3], (1, 2), 0.9279044041208528)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 4, 0], (2, 3), 0.9374998807870725)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 1, 0], (1, 1), 0.9999999999999991)
AI Made Random Choice
Playing training game 589
AI Q-Learning Choice: ([1, 3, 5, 7], (3, 2), 1.842878772616234e-10)
AI Q-Learning Choice: ([1, 3, 5, 5], (3, 2), 0.9393173813850547)
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 1), 5.072879365185051e-12)
AI Q-Learning Choice: ([1, 3, 4, 3], (1, 2), 0.9327021424539627)
AI Made Random Choice
AI Q-Learning Choice: (

...

AI Q-Learning Choice: ([1, 3, 4, 7], (1, 1), 0.9999999984755852)
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 4, 2], (2, 3), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 1, 2], (3, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 1, 1], (3, 1), 1.0)
AI Made Random Choice
Playing training game 9274
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 5, 7], (2, 1), 0.9999999237382133)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 4, 7], (3, 2), 0.9999997570445627)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 4, 4], (0, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 4, 3], (2, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 3], (3, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 1], (2, 2), 1.0)
AI Made Random Choice
Playing training game 9275
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 4), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 1, 2], (1, 1), 1.0)
AI Made Random 

AI Q-Learning Choice: ([1, 3, 5, 6], (0, 1), 0.9999994618899813)
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 3, 6], (3, 6), 0.9999998807904771)
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 1, 0], (1, 3), 0.9999999999999998)
AI Made Random Choice
Playing training game 9428
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 3], (2, 4), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 0, 3], (1, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 0, 0], (1, 2), 1.0)
AI Made Random Choice
Playing training game 9429
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 5, 7], (1, 1), 0.9999999987356618)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 5, 7], (3, 3), 0.9999999295569499)
AI Made Random Choice
AI Q-Learning Choice: ([0, 1, 3, 4], (3, 2), 0.9999999944083837)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 3, 2], (2, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 0, 2], (3, 1), 1.0)
AI Made Random Choice
Playing training gam

AI Made Random Choice
Playing training game 9653
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 5, 7], (1, 1), 0.9999903798767735)
AI Made Random Choice
AI Q-Learning Choice: ([0, 2, 5, 5], (1, 2), 0.9999999969975444)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 5, 2], (2, 3), 0.9999999981373549)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 1], (2, 2), 1.0)
AI Made Random Choice
Playing training game 9654
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 2], (2, 5), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 0, 2], (0, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 0, 2], (3, 1), 1.0)
AI Made Random Choice
Playing training game 9655
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 1, 7], (3, 4), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 0, 3], (1, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 0, 0], (1, 2), 1.0)
AI Made Random Choice
Playing training game 9656
AI Made Random Choice
AI Q-Learning Cho

AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 0, 2], (3, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 0, 0], (1, 1), 1.0)
AI Made Random Choice
Playing training game 9797
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 2], (2, 5), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 0, 1], (1, 2), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 0, 1], (3, 1), 1.0)
AI Made Random Choice
Playing training game 9798
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 5, 7], (3, 2), 0.9999999983197208)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 5, 0], (2, 4), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([1, 1, 0, 0], (1, 1), 1.0)
AI Made Random Choice
Playing training game 9799
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 6], (0, 1), 0.9999957997515533)
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 4, 6], (1, 1), 0.9994695392338402)
AI Made Random Choice
AI Q-Learning Choice: ([0, 2, 2, 6], (3, 6), 0.9999997615814209)
A

Playing training game 9979
AI Made Random Choice
AI Q-Learning Choice: ([1, 2, 5, 7], (2, 1), 0.9999999544607885)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 4, 7], (3, 2), 0.999999947744717)
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 4, 4], (0, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 1, 4], (3, 4), 1.0)
AI Made Random Choice
Playing training game 9980
AI Made Random Choice
AI Q-Learning Choice: ([1, 3, 5, 6], (0, 1), 0.9999915652437518)
AI Made Random Choice
AI Q-Learning Choice: ([0, 3, 5, 5], (1, 3), 0.9999999317789666)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 3, 5], (3, 2), 0.9999999925492697)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 3, 1], (2, 3), 1.0)
AI Made Random Choice
Playing training game 9981
AI Made Random Choice
AI Q-Learning Choice: ([1, 0, 5, 7], (3, 3), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 5, 4], (2, 1), 1.0)
AI Made Random Choice
AI Q-Learning Choice: ([0, 0, 2, 4], (3, 2), 1.0)
AI Made R

In [47]:
play(ai)


Piles:
Pile 0: 1
Pile 1: 3
Pile 2: 5
Pile 3: 7

AI's Turn
AI Made Random Choice
AI chose to take 4 from pile 2.

Piles:
Pile 0: 1
Pile 1: 3
Pile 2: 1
Pile 3: 7

Your Turn
Choose Pile: 2
Choose Count: 1

Piles:
Pile 0: 1
Pile 1: 3
Pile 2: 0
Pile 3: 7

AI's Turn
AI Q-Learning Choice: ([1, 3, 0, 7], (3, 5), 1.0)
AI chose to take 5 from pile 3.

Piles:
Pile 0: 1
Pile 1: 3
Pile 2: 0
Pile 3: 2

Your Turn
Choose Pile: 1
Choose Count: 1

Piles:
Pile 0: 1
Pile 1: 2
Pile 2: 0
Pile 3: 2

AI's Turn
AI Q-Learning Choice: ([1, 2, 0, 2], (0, 1), 1.0)
AI chose to take 1 from pile 0.

Piles:
Pile 0: 0
Pile 1: 2
Pile 2: 0
Pile 3: 2

Your Turn
Choose Pile: 3
Choose Count: 1

Piles:
Pile 0: 0
Pile 1: 2
Pile 2: 0
Pile 3: 1

AI's Turn
AI Q-Learning Choice: ([0, 2, 0, 1], (1, 2), 1.0)
AI chose to take 2 from pile 1.

Piles:
Pile 0: 0
Pile 1: 0
Pile 2: 0
Pile 3: 1

Your Turn
Choose Pile: 3
Choose Count: 1

GAME OVER
Winner is AI
